# AVALIAÇÃO 3 - PROGRAMAÇÃO EM FINANÇAS
#### Professor: Julio Russo
#### Disciplina: Programação em Finanças
#### Turma: 2025.1
#### Alunos: Lucas dos Santos Marques, Luiz Fernando M. Meirinho , Victor A. S. de Souza e Victor Flávio P. Dornelos
#### Data: 25/06/2025

## 1 - Preparando os dados

In [1]:
import pandas as pd
import numpy as np
import yfinance as yf
import plotly.express as px
from tabulate import tabulate
import time

### Premissas da criação da carteira

#### **Carteira Brasileira**

- Foi utilizada como referência o **ETF NSDV11**, que segue o **índice Bovespa Smart Dividendos B3**. Esse índice visa **mensurar o desempenho médio das ações brasileiras que mais remuneram seus investidores**, seja por **dividendos** ou **juros sobre capital próprio**.
- A premissa adotada foi utilizar **empresas presentes nesse índice como um proxy de qualidade**, visto que a **distribuição recorrente de dividendos, isenta de impostos**, atrai tanto investidores quanto as próprias empresas que buscam valorização e liquidez.
- Foram selecionadas **5 empresas** desse índice, **cada uma de um setor diferente**, para compor a carteira.
- O objetivo da carteira é **superar o desempenho do índice de mercado**, representado pelo **Ibovespa**.

---

#### **Carteira Americana**

- Foi utilizada como referência o **ETF QUAL**, que replica o **índice MSCI USA Quality Factor**, o qual contempla **empresas americanas de alta qualidade**, com critérios como **baixa alavancagem** e **lucros consistentes ao longo do tempo**.
- A estratégia foi selecionar as **8 maiores empresas** desse índice, pertencentes aos **8 principais setores da economia americana**, garantindo assim **diversificação setorial**. Foi escolhida **1 empresa por setor**.
- A meta é montar uma carteira que consiga **superar o desempenho do índice de mercado americano**, no caso, o **S&P 500**.

In [2]:
# Carteira brasileira e Benchmark
acoes_br = ['BBDC4.SA','CMIG4.SA','PETR4.SA','GOAU4.SA','MRFG3.SA', '^BVSP']
# Baixar os dados
df_completo = yf.download(acoes_br,auto_adjust=True,start='2014-01-01',end='2024-12-31')['Close']

# Separar carteira e benchmark
df_br = df_completo[['BBDC4.SA','CMIG4.SA','PETR4.SA','GOAU4.SA','MRFG3.SA']]
df_ibov = df_completo[['^BVSP']]


# Salvando em CSV (Opcional, mas boa prática)
df_br.to_csv('carteira_brasileira.csv')
df_ibov.to_csv('ibovespa.csv')

[*********************100%***********************]  6 of 6 completed


In [3]:
# Carteira EUA corrigida (apenas tickers válidos)
acoes_eua_completo = ['NVDA', 'V', 'LLY', 'META', 'TJX', 'COST','ADP','JNJ','^GSPC']

# Baixar os dados de fechamento ajustado
df_completo = yf.download(acoes_eua_completo, auto_adjust=True, start='2014-01-01', end='2024-12-31')['Close']

# --- 2. Separar os dados da Carteira e do Benchmark ---
acoes_eua = ['NVDA', 'V', 'LLY', 'META', 'TJX', 'COST','ADP','JNJ']
df_eua = df_completo[acoes_eua]
df_sp500 = df_completo[['^GSPC']]

# Salvar em CSVs separados
df_eua.to_csv('carteira_eua.csv')
df_sp500.to_csv('sp500.csv')

[*********************100%***********************]  9 of 9 completed


## PARTE 1 - AÇÕES BRASIL

### QUESTÃO 1:
Formação de portfólio com ações brasileiras (mínimo 4 ativos). Não é necessário ter os mesmo pesos iniciais.


In [4]:
# Importando os dados
df_br = pd.read_csv('carteira_brasileira.csv', index_col='Date', parse_dates=True)
df_ibov = pd.read_csv('ibovespa.csv', index_col='Date', parse_dates=True)

pesos_br = np.array([0.26, 0.21, 0.20, 0.19,0.14])

### QUESTÃO 2:
Analisar retornos, volatilidade(desv.pad) dos ativos e da carteira

In [5]:
# Retornos logarítmicos diários
retornos_diarios_carteira = np.log(df_br / df_br.shift(1)).dropna()
retornos_diarios_ibov = np.log(df_ibov / df_ibov.shift(1)).dropna()

# Indicadores individuais
retorno_anual = retornos_diarios_carteira.mean() * 252
retorno_acumulado = (df_br.iloc[-1] / df_br.iloc[0]) - 1
desvio_padrao_anual = retornos_diarios_carteira.std() * np.sqrt(252)
coef_variacao = desvio_padrao_anual / retorno_anual

In [6]:
# Tabela por ativo
tabela_ativos = pd.DataFrame({
    'Retorno Anual (%)': retorno_anual * 100,
    'Retorno Acumulado (%)': retorno_acumulado * 100,
    'Desvio Padrão Anual (%)': desvio_padrao_anual * 100,
    'Coef. de Variação': coef_variacao
})

In [7]:
# --- Indicadores da Carteira ---
retorno_portfolio_diario = retornos_diarios_carteira @ pesos_br
retorno_anual_ptf = retorno_portfolio_diario.mean() * 252
retorno_acumulado_ptf = np.exp(retorno_portfolio_diario.cumsum())[-1] - 1
desvio_padrao_ptf = retorno_portfolio_diario.std() * np.sqrt(252)
coef_variacao_ptf = desvio_padrao_ptf / retorno_anual_ptf

/var/folders/wk/k6089y_d7hv_rwb2m8vbm9cr0000gn/T/ipykernel_5016/1535098392.py:4: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  retorno_acumulado_ptf = np.exp(retorno_portfolio_diario.cumsum())[-1] - 1


In [8]:
# Adiciona à tabela
tabela_ativos.loc['Carteira'] = [
    retorno_anual_ptf * 100,
    retorno_acumulado_ptf * 100,
    desvio_padrao_ptf * 100,
    coef_variacao_ptf
]

In [9]:
# --- Indicadores do Benchmark (IBOV) ---
retorno_anual_ibov = retornos_diarios_ibov.mean() * 252
retorno_acumulado_ibov = (df_ibov.iloc[-1] / df_ibov.iloc[0]) - 1
desvio_padrao_anual_ibov = retornos_diarios_ibov.std() * np.sqrt(252)
coef_variacao_ibov = desvio_padrao_anual_ibov / retorno_anual_ibov

In [10]:
# Adiciona à tabela
tabela_ativos.loc['Benchmark (IBOV)'] = [
    retorno_anual_ibov.iloc[0] * 100,
    retorno_acumulado_ibov.iloc[0] * 100,
    desvio_padrao_anual_ibov.iloc[0] * 100,
    coef_variacao_ibov.iloc[0]
]

In [11]:
# Arredondar para melhor visualização
tabela_ativos = tabela_ativos.round(2)

In [12]:
#  Taxa livre de risco (ajuste conforme o país e período)
r_f = 0.0945  # CDI Médio de 2014 a 2024

# --- Sharpe Ratio ---
# Sharpe dos ativos
sharpe_ativos = (retorno_anual - r_f) / desvio_padrao_anual
tabela_ativos['Sharpe Ratio'] = sharpe_ativos

# Sharpe da carteira
sharpe_portfolio = (retorno_anual_ptf - r_f) / desvio_padrao_ptf
tabela_ativos.loc['Carteira', 'Sharpe Ratio'] = sharpe_portfolio

# Sharpe do IBOV
sharpe_ibov = (retorno_anual_ibov - r_f) / desvio_padrao_anual_ibov
tabela_ativos.loc['Benchmark (IBOV)', 'Sharpe Ratio'] = sharpe_ibov.iloc[0]


# Arredondar para melhor visualização
tabela_ativos = tabela_ativos.round(2)


# Exibe com tabulate
print("\n📊 Indicadores com Sharpe Ratio:\n")
print(tabulate(tabela_ativos, headers='keys', tablefmt='fancy_grid'))


📊 Indicadores com Sharpe Ratio:

╒══════════════════╤═════════════════════╤═════════════════════════╤═══════════════════════════╤═════════════════════╤════════════════╕
│                  │   Retorno Anual (%) │   Retorno Acumulado (%) │   Desvio Padrão Anual (%) │   Coef. de Variação │   Sharpe Ratio │
╞══════════════════╪═════════════════════╪═════════════════════════╪═══════════════════════════╪═════════════════════╪════════════════╡
│ BBDC4.SA         │                1.51 │                   17.77 │                     35.62 │               23.62 │          -0.22 │
├──────────────────┼─────────────────────┼─────────────────────────┼───────────────────────────┼─────────────────────┼────────────────┤
│ CMIG4.SA         │               13.83 │                  348.47 │                     41.54 │                3    │           0.11 │
├──────────────────┼─────────────────────┼─────────────────────────┼───────────────────────────┼─────────────────────┼────────────────┤
│ PETR4.SA    

### QUESTÃO 3:
Construção dos gráficos em plotly de retorno e gráfico PIE das participações relativas das ações no portfólio.

In [13]:
portfolio_tickers = ['BBDC4.SA','CMIG4.SA','PETR4.SA','GOAU4.SA','MRFG3.SA']
pesos_br = np.array([0.26, 0.21, 0.20, 0.19,0.14])

In [14]:
# 1. DataFrame para o Gráfico de Pizza
df_pie = pd.DataFrame({
    'Ativo': portfolio_tickers, 
    'Peso': pesos_br
})

In [15]:

cores_personalizadas_br = {
    'BBDC4': '#005a9e',      # Azul (Bradesco)
    'CMIG4': '#ffc72c',      # Amarelo (Cemig)
    'PETR4': '#00a859',      # Verde (Petrobras)
    'GOAU4': '#f47d31',      # Laranja (Gerdau)
    'MRFG3': '#d52b1e',      # Vermelho (Marfrig)
    'Carteira': 'purple'     # Roxo para a carteira
}

In [16]:
df_br = pd.read_csv('carteira_brasileira.csv', index_col='Date', parse_dates=True)

In [17]:
# Normalizar os ativos
df_norm = (df_br / df_br.iloc[0]) * 100
df_norm = df_norm.reset_index().melt(id_vars='Date', var_name='Ativo', value_name='Rentabilidade Normalizada (%)')


In [18]:
# Calcular o valor normalizado da carteira
pesos = np.array([0.26, 0.21, 0.20, 0.19,0.14])
port_br = df_br @ pesos
port_br_norm = (port_br / port_br.iloc[0]) * 100
df_port = port_br_norm.reset_index().rename(columns={0: 'Rentabilidade Normalizada (%)'})
df_port['Ativo'] = 'Carteira'

In [19]:
# Unir dados
df_total = pd.concat([df_norm, df_port], ignore_index=True)


In [20]:
df_plot =  df_br.reset_index().melt(id_vars='Date', var_name='Ativo', value_name='Preço')

In [41]:
import plotly.graph_objects as go

# --------- Tela Inicial ---------
tela_inicial = go.Indicator(
    title={"text": "Selecione um gráfico acima"},
    number={"font": {"color": "lightgray"}},
    domain={"x": [0, 1], "y": [0, 1]}
)

# --------- Pizza ---------
pizza = go.Pie(
    labels=[i for i in df_pie['Ativo']],
    values=df_pie['Peso'],
    name='Participações',
    marker_colors=[cores_personalizadas_br.get(i, 'gray') for i in df_pie['Ativo']],
    textinfo='percent+label',
    hole=0
)

# --------- Preço ---------
linhas_preco = [
    go.Scatter(
        x=df_plot[df_plot['Ativo'] == ativo]['Date'],
        y=df_plot[df_plot['Ativo'] == ativo]['Preço'],
        name=ativo.replace('.SA', ''),
        mode='lines',
        line=dict(color=cores_personalizadas_br.get(ativo.replace('.SA', ''), 'gray'))  # fallback: gray
    )
    for ativo in df_plot['Ativo'].unique()
]

# --------- Rentabilidade ---------
linhas_rent = [
    go.Scatter(
        x=df_total[df_total['Ativo'] == ativo]['Date'],
        y=df_total[df_total['Ativo'] == ativo]['Rentabilidade Normalizada (%)'],
        name=ativo.replace('.SA', ''),
        mode='lines',
        line=dict(color=cores_personalizadas_br.get(ativo.replace('.SA', ''), 'gray'))
    )
    for ativo in df_total['Ativo'].unique()
]

# --------- Layout ---------
layout = go.Layout(
    title='Gráficos Interativos de Ações',
    hovermode='x unified',
    xaxis=dict(visible=False),
    yaxis=dict(visible=False),
    height=600,
    width=1000,
    updatemenus=[
        dict(
            type='buttons',
            direction='right',
            showactive=True,
            x=0,
            xanchor='left',
            y=1.05,
            yanchor='top',
            pad={'r': 10, 't': 10},
            buttons=[
                dict(label='Pizza',
                     method='update',
                     args=[{'visible': [False, True] + [False]*len(linhas_preco) + [False]*len(linhas_rent)},
                           {'title': 'Participações Relativas das Ações no Portfólio',
                            'xaxis': {'visible': False},
                            'yaxis': {'visible': False}}]),
                dict(label='Preço',
                     method='update',
                     args=[{'visible': [False, False] + [True]*len(linhas_preco) + [False]*len(linhas_rent)},
                           {'title': 'Evolução do Preço das Ações no Portfólio',
                            'xaxis': {'visible': True, 'rangeslider': {'visible': True}},
                            'yaxis': {'visible': True}}]),
                dict(label='Rentabilidade',
                     method='update',
                     args=[{'visible': [False, False] + [False]*len(linhas_preco) + [True]*len(linhas_rent)},
                           {'title': 'Rentabilidade Normalizada dos Ativos e da Carteira',
                            'xaxis': {'visible': True, 'rangeslider': {'visible': True}},
                            'yaxis': {'visible': True}}])
            ]
        )
    ]
)

# --------- Criar figura ---------
fig = go.Figure(data=[tela_inicial, pizza] + linhas_preco + linhas_rent, layout=layout)

# Visibilidade inicial: apenas a mensagem
visibility = [True, False] + [False]*(len(linhas_preco) + len(linhas_rent))
for i, trace in enumerate(fig.data):
    trace.visible = visibility[i]

fig.show()

## PARTE 2

### QUESTÃO 4
Formação de portfólio com ações americanas (mínimo 7 ativos). Não é necessário ter os mesmo pesos iniciais

In [22]:
# Importando os dados
df_eua = pd.read_csv('carteira_eua.csv', index_col='Date', parse_dates=True)
df_sp500 = pd.read_csv('sp500.csv', index_col='Date', parse_dates=True)
pesos_eua = np.array([0.25, 0.17, 0.15, 0.14, 0.09, 0.07, 0.07,0.06])

### QUESTÃO 5
Analisar retornos, volatilidade(desv.pad) dos ativos e da carteira

In [23]:
# Retornos logarítmicos diários
retornos_diarios_carteira = np.log(df_eua / df_eua.shift(1)).dropna()

# Indicadores individuais
retorno_anual = retornos_diarios_carteira.mean() * 252
retorno_acumulado = (df_eua.iloc[-1] / df_eua.iloc[0]) - 1
desvio_padrao_anual = retornos_diarios_carteira.std() * np.sqrt(252)
coef_variacao = desvio_padrao_anual / retorno_anual

In [24]:
# Tabela por ativo
tabela_ativos = pd.DataFrame({
    'Retorno Anual (%)': retorno_anual * 100,
    'Retorno Acumulado (%)': retorno_acumulado * 100,
    'Desvio Padrão Anual (%)': desvio_padrao_anual * 100,
    'Coef. de Variação': coef_variacao
})

In [25]:
# Retorno do portfólio
retorno_portfolio_diario = retornos_diarios_carteira @ pesos_eua
retorno_anual_ptf = retorno_portfolio_diario.mean() * 252
retorno_acumulado_ptf = np.exp(retorno_portfolio_diario.cumsum())[-1] - 1
desvio_padrao_ptf = retorno_portfolio_diario.std() * np.sqrt(252)
coef_variacao_ptf = desvio_padrao_ptf / retorno_anual_ptf

/var/folders/wk/k6089y_d7hv_rwb2m8vbm9cr0000gn/T/ipykernel_5016/1855388707.py:4: FutureWarning:

Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`



In [26]:
# Adiciona à tabela
tabela_ativos.loc['Carteira'] = [
    retorno_anual_ptf * 100,
    retorno_acumulado_ptf * 100,
    desvio_padrao_ptf * 100,
    coef_variacao_ptf
]

In [27]:
retornos_diarios_sp500 = np.log(df_sp500 / df_sp500.shift(1)).dropna()

In [28]:
# --- 3. Bloco de cálculo para o S&P 500 ---
retorno_anual_sp500 = retornos_diarios_sp500.mean() * 252
retorno_acumulado_sp500 = (df_sp500.iloc[-1] / df_sp500.iloc[0]) - 1
desvio_padrao_anual_sp500 = retornos_diarios_sp500.std() * np.sqrt(252)
coef_variacao_sp500 = desvio_padrao_anual_sp500 / retorno_anual_sp500

In [29]:
# Adiciona o S&P 500 à tabela
tabela_ativos.loc['Benchmark (S&P 500)'] = [
    retorno_anual_sp500.iloc[0] * 100,
    retorno_acumulado_sp500.iloc[0] * 100,
    desvio_padrao_anual_sp500.iloc[0] * 100,
    coef_variacao_sp500.iloc[0]
]

In [30]:
# Arredondar para melhor visualização
tabela_ativos = tabela_ativos.round(2)

In [31]:
# Taxa livre de risco
r_f = 0.0165

# --- 4. Sharpe Ratio para o S&P 500 ---
# Sharpe dos ativos
sharpe_ativos = (retorno_anual - r_f) / desvio_padrao_anual
tabela_ativos['Sharpe Ratio'] = sharpe_ativos

# Sharpe da carteira
sharpe_portfolio = (retorno_anual_ptf - r_f) / desvio_padrao_ptf
tabela_ativos.loc['Carteira', 'Sharpe Ratio'] = sharpe_portfolio

# Sharpe do S&P 500
sharpe_sp500 = (retorno_anual_sp500 - r_f) / desvio_padrao_anual_sp500
tabela_ativos.loc['Benchmark (S&P 500)', 'Sharpe Ratio'] = sharpe_sp500.iloc[0]

# Exibe com tabulate
print("\n📊 Indicadores da Carteira Americana com Sharpe Ratio:\n")
print(tabulate(tabela_ativos.round(2), headers='keys', tablefmt='fancy_grid'))


📊 Indicadores da Carteira Americana com Sharpe Ratio:

╒═════════════════════╤═════════════════════╤═════════════════════════╤═══════════════════════════╤═════════════════════╤════════════════╕
│                     │   Retorno Anual (%) │   Retorno Acumulado (%) │   Desvio Padrão Anual (%) │   Coef. de Variação │   Sharpe Ratio │
╞═════════════════════╪═════════════════════╪═════════════════════════╪═══════════════════════════╪═════════════════════╪════════════════╡
│ NVDA                │               53.82 │                36665.4  │                     46.59 │                0.87 │           1.12 │
├─────────────────────┼─────────────────────┼─────────────────────────┼───────────────────────────┼─────────────────────┼────────────────┤
│ V                   │               16.57 │                  516.66 │                     24.12 │                1.46 │           0.62 │
├─────────────────────┼─────────────────────┼─────────────────────────┼───────────────────────────┼───────────

### QUESTÃO 6
Construção dos gráficos em plotly de retorno e gráfico PIE das participações relativas das ações no portfólio.

In [32]:
# Apenas os tickers e pesos da carteira para os gráficos
portfolio_tickers_eua = ['NVDA', 'V', 'LLY', 'META', 'TJX', 'COST','ADP','JNJ']
pesos_eua = np.array([0.25, 0.17, 0.15, 0.14, 0.09, 0.07, 0.07,0.06])

In [33]:
# 1. DataFrame para o Gráfico de Pizza
df_pie = pd.DataFrame({
    'Ativo': portfolio_tickers_eua,
    'Peso': pesos_eua
})

In [34]:
df_eua = pd.read_csv('carteira_eua.csv', index_col='Date', parse_dates=True)

In [35]:
# Normalizar os ativos
df_norm = (df_eua / df_eua.iloc[0]) * 100
df_norm = df_norm.reset_index().melt(id_vars='Date', var_name='Ativo', value_name='Rentabilidade Normalizada (%)')


In [36]:
# Calcular o valor normalizado da carteira
port_eua = df_eua @ pesos_eua
port_eua_norm = (port_eua / port_eua.iloc[0]) * 100
df_port = port_eua_norm.reset_index().rename(columns={0: 'Rentabilidade Normalizada (%)'})
df_port['Ativo'] = 'Carteira'

In [37]:
df_plot_eua =  df_eua.reset_index().melt(id_vars='Date', var_name='Ativo', value_name='Preço')

In [38]:
# Unir dados
df_total = pd.concat([df_norm, df_port], ignore_index=True)


In [40]:
import plotly.graph_objects as go

# --------- Cores Personalizadas EUA ---------
cores_personalizadas_eua = {
    'NVDA': '#76B900',     # Verde (NVIDIA)
    'V': '#1A1F71',        # Azul (Visa)
    'LLY': '#00A9E0',      # Azul claro (Eli Lilly)
    'META': '#1877F2',     # Azul (Meta/Facebook)
    'TJX': '#C8102E',      # Vermelho (TJX Companies)
    'COST': '#E41A2B',     # Vermelho (Costco)
    'ADP': '#ED1C24',      # Vermelho (ADP)
    'JNJ': '#D41E2A',      # Vermelho (Johnson & Johnson)
    'Carteira': 'purple'   # Roxo
}

# --------- Tela Inicial: Indicador com texto ---------
tela_inicial = go.Indicator(
    title={"text": "<b>Selecione um gráfico acima</b>"},
    number={"font": {"color": "lightgray"}},
    domain={"x": [0, 1], "y": [0, 1]}
)

# --------- Gráfico de Pizza ---------
pizza = go.Pie(
    labels=df_pie['Ativo'],
    values=df_pie['Peso'],
    name='Participações',
    marker_colors=[cores_personalizadas_eua.get(i, 'gray') for i in df_pie['Ativo']],
    textinfo='percent+label',
    hole=0
)

# --------- Gráfico de Preço ---------
linhas_preco = [
    go.Scatter(
        x=df_plot_eua[df_plot_eua['Ativo'] == ativo]['Date'],
        y=df_plot_eua[df_plot_eua['Ativo'] == ativo]['Preço'],
        name=ativo,
        mode='lines',
        line=dict(color=cores_personalizadas_eua.get(ativo, 'gray'))
    )
    for ativo in df_plot_eua['Ativo'].unique()
]

# --------- Gráfico de Rentabilidade ---------
linhas_rent = [
    go.Scatter(
        x=df_total[df_total['Ativo'] == ativo]['Date'],
        y=df_total[df_total['Ativo'] == ativo]['Rentabilidade Normalizada (%)'],
        name=ativo,
        mode='lines',
        line=dict(color=cores_personalizadas_eua.get(ativo, 'gray'))
    )
    for ativo in df_total['Ativo'].unique()
]

# --------- Layout com Botões ---------
layout = go.Layout(
    title='Gráficos Interativos de Ações',
    hovermode='x unified',
    xaxis=dict(visible=False),
    yaxis=dict(visible=False),
    height=600,
    width=1000,
    updatemenus=[
        dict(
            type='buttons',
            direction='right',
            showactive=True,
            x=0,
            xanchor='left',
            y=1.05,
            yanchor='top',
            pad={'r': 10, 't': 10},
            buttons=[
                dict(label='Pizza',
                     method='update',
                     args=[{'visible': [False, True] + [False]*len(linhas_preco) + [False]*len(linhas_rent)},
                           {'title': 'Participações Relativas das Ações no Portfólio',
                            'xaxis': {'visible': False},
                            'yaxis': {'visible': False}}]),
                dict(label='Preço',
                     method='update',
                     args=[{'visible': [False, False] + [True]*len(linhas_preco) + [False]*len(linhas_rent)},
                           {'title': 'Evolução do Preço das Ações no Portfólio',
                            'xaxis': {'visible': True, 'rangeslider': {'visible': True}},
                            'yaxis': {'visible': True}}]),
                dict(label='Rentabilidade',
                     method='update',
                     args=[{'visible': [False, False] + [False]*len(linhas_preco) + [True]*len(linhas_rent)},
                           {'title': 'Rentabilidade Normalizada dos Ativos e da Carteira',
                            'xaxis': {'visible': True, 'rangeslider': {'visible': True}},
                            'yaxis': {'visible': True}}])
            ]
        )
    ]
)

# --------- Criar Figura ---------
fig = go.Figure(data=[tela_inicial, pizza] + linhas_preco + linhas_rent, layout=layout)

# Visibilidade inicial: somente a mensagem
visibility = [True, False] + [False]*(len(linhas_preco) + len(linhas_rent))
for i, trace in enumerate(fig.data):
    trace.visible = visibility[i]

# Exibir
fig.show()